In [1]:
# To make it easier
label_mappings = {0: "chihuahua", 1: "muffin"}

Case Studies we take a look at:
- VGG-16 (from Keras models repository, fine tuned)
- XCeption

> https://www.topbots.com/important-cnn-architectures/

In [2]:
# https://keras.io/guides/transfer_learning/

## Utility functions


In [18]:
from torchvision.datasets import ImageFolder
from keras.src import Functional
from typing import Callable
import plotly.express as px
import torch
import numpy as np


def make_evaluations_list(evaluate_model: Callable[[any, Functional], any], model: Functional,
                          reference_dataset: ImageFolder, samples: int = 8) -> list[tuple[any, any, any]]:
    """
    
    :param evaluate_model: 
    :param model: 
    :param reference_dataset: 
    :param samples: 
    :return: A tuple containing: [the image ready for plotting, the predicted label from the model, the true label]
    """
    for i in torch.rand(samples):
        # Random draw
        random_index = int(i * (len(reference_dataset)))

        img = reference_dataset[random_index][0]
        label = reference_dataset[random_index][1]
        yield torch.permute(img, (1, 2, 0)), evaluate_model(img, model), label


def print_evaluation_lists_information(image_evaluations_list: list[tuple[any, any, any]]) -> None:
    current_index = 0
    images = []

    for img, pred, y in image_evaluations_list:
        images.append(img)

        print(f"For facet {current_index} model has predicted: {[pred_entry[1] for pred_entry in pred]}. "
              f"The correct label is {y}")

        current_index += 1

    image_show = px.imshow(np.array(images), binary_string=True, facet_col=0, facet_col_wrap=4)
    image_show.show()

# 1 - Xception
Before training and fine tuning lets see the performance of the pretrained model on some samples.

In [1]:
project_definition: dict[str, any] = {"name": "xception"}
# Our Xception default values. We had to reduce batch size or else we weren't able to work.
default_values = {"batch_size": 16, "epochs": 15, "learning_rate": 1e-2}

In [5]:
import keras

# Setting weights of course requires downloading them from the source (Keras is our mirror as we work with their libraries)
untouched_xception = keras.applications.Xception(weights='imagenet')

In [6]:
import numpy


def evaluate_xception(image, xception, verbose: bool = False):
    local_image = torch.permute(image, (1, 2, 0))
    local_image = numpy.expand_dims(local_image, 0)

    return keras.applications.xception.decode_predictions(xception.predict(local_image, verbose=verbose), top=3)[0]

## 1.2 - Data loading for Xception

In [2]:
from torch.utils.data import DataLoader
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper
import torch

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((299, 299))

# Todo valuta se metterlo.
# Optionally fix the generator for reproducible results, e.g.: torch.Generator().manual_seed(42)
train, validation = torch.utils.data.random_split(train, [0.875, 0.125])

train_dataloader = DataLoader(dataset=train, batch_size=default_values["batch_size"], shuffle=True)
validation_dataloader = DataLoader(dataset=validation, batch_size=default_values["batch_size"], shuffle=True)
test_dataloader = DataLoader(dataset=test, batch_size=default_values["batch_size"], shuffle=True)

We don't need to calculate the mean and variance of the dataset as we use a pre-trained model.

It is required to use mean/variance of the data xception used (as in the pre-process pipe).

## 1.1 -  Model Evaluation without training

In [8]:
print_evaluation_lists_information(make_evaluations_list(evaluate_xception, untouched_xception, train))

/home/jacopo/miniconda3/envs/keras-pytorch/lib/python3.12/site-packages/keras/src/backend/torch/nn.py:412: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at /opt/conda/conda-bld/pytorch_1704987296916/work/aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  outputs = tnn.conv2d(


For facet 0 model has predicted: ['goblet', 'cocktail_shaker', 'titi']. The correct label is 0
For facet 1 model has predicted: ['bakery', 'potpie', 'plate']. The correct label is 1
For facet 2 model has predicted: ['miniature_pinscher', 'Chihuahua', 'kelpie']. The correct label is 0
For facet 3 model has predicted: ['mask', 'sunglass', 'comic_book']. The correct label is 0
For facet 4 model has predicted: ['plate', 'menu', 'Petri_dish']. The correct label is 1
For facet 5 model has predicted: ['Chihuahua', 'toy_terrier', 'Brabancon_griffon']. The correct label is 0
For facet 6 model has predicted: ['marmot', 'hare', 'beaver']. The correct label is 0
For facet 7 model has predicted: ['packet', 'eggnog', 'rotisserie']. The correct label is 1


In [9]:
# The model does not recognize Muffins as being muffins just as bakery (Which makes sense)
# As the label Muffin is missing in the decoding of the Xception we just map it to bakery

In [10]:
predictions: list[tuple[list, int]] = [(evaluate_xception(i[0], untouched_xception), i[1]) for i in test]

In [11]:
# Redefine the labels to fit the observations on Xception
label_mappings = {0: ["chihuahua", "dog"], 1: ["muffin", "bakery"]}

TP = 0  # True positives
for i in range(len(predictions)):
    predicted_values = [j[1].lower() for j in predictions[i][0]]
    true_label = label_mappings[predictions[i][1]]

    TP += 1 if set(predicted_values) & set(true_label) else 0

precision = TP / len(predictions)
precision  # On the top 3 considering the fact that many miss classifications happen for the fact that the labels are more accurate for the dogs (some samples in the training set are not chihuahuas) and that Muffins do not have a real label.

0.6427364864864865

## 1.2 - Fine tuning the model
We follow the following guide: https://keras.io/guides/transfer_learning/

### 1.2.1 - Model definition

> Note: each Keras Application expects a specific kind of input preprocessing. For Xception, call keras.applications.xception.preprocess_input on your inputs before passing them to the model. xception.preprocess_input will scale input pixels between -1 and 1

#### Note:
While Keras documents to use ```keras.applications.xception.preprocess_input(x, mode='torch')```
we cannot use it with our loading functions as it requires input to not be scaled to tensor!

So we simply workaround it by applying the ```tf``` procedure.

In [2]:
from models.structure.base_model_wrapper import BaseModelWrapper
import keras
from keras.src import Functional


# https://keras.io/guides/transfer_learning/#the-typical-transferlearning-workflow 
# With augmentation just to permute here
class XceptionAugmented(BaseModelWrapper):
    latest_xception_model: Functional

    def make_layers(self, input_shape: (int, int, int)) -> tuple[keras.Layer, keras.Layer]:
        C, W, H = input_shape

        inputs = keras.Input(input_shape)

        x = keras.layers.Permute((2, 3, 1))(inputs)

        # Augmentation process.
        x = keras.layers.RandomFlip(mode="horizontal_and_vertical")(x)
        x = keras.layers.RandomRotation(0.3)(x)
        x = keras.layers.RandomBrightness(0.4, value_range=(0., 1.))(x)

        x = keras.layers.Rescaling(scale=1 / 2, offset=-1)(x)

        self.latest_xception_model = keras.applications.Xception(
            weights='imagenet', include_top=False, input_shape=(W, H, C)
        )

        self.latest_xception_model.trainable = False
        x = self.latest_xception_model(x, training=False)
        x = keras.layers.GlobalAveragePooling2D()(x)

        outputs = keras.layers.Dense(1, activation='sigmoid')(x)
        return inputs, outputs

### 1.2.2 - Training and evaluation only on appended structure

In [5]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

xception_aug = XceptionAugmented()
model = xception_aug.make_model((3, 299, 299))

learning_parameters = SgdLearningParameters(learning_rate=0.01, momentum=0.9, metrics=["accuracy", ZeroOneLoss()])
learning_parameters.compile_model(model)

model.summary()

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)        │ (None, 3, 299, 299)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ permute (Permute)               │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_flip (RandomFlip)        │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_rotation                 │ (None, 299, 299, 3)    │             0 │
│ (RandomRotation)                │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_brightness               │ (None, 299, 299, 3)    │             0 │
│ (RandomBrightness)              │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ rescaling (Rescaling)           │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ xception (Functional)           │ (None, 10, 10, 2048)   │    20,861,480 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ global_average_pooling2d        │ (None, 2048)           │             0 │
│ (GlobalAveragePooling2D)        │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │         2,049 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 20,863,529 (79.59 MB)

 Trainable params: 2,049 (8.00 KB)

 Non-trainable params: 20,861,480 (79.58 MB)

In [6]:
history = model.fit(train_dataloader, epochs=5, validation_data=validation_dataloader, callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True),
    keras.callbacks.EarlyStopping(monitor='val_loss', patience=2, verbose=1, mode='min')
])

Epoch 1/5
  1/259 ━━━━━━━━━━━━━━━━━━━━ 1:36 372ms/step - accuracy: 0.6250 - loss: 0.6757 - total_0-1_loss: 6.0000

/home/jacopo/miniconda3/envs/keras-pytorch/lib/python3.12/site-packages/keras/src/backend/torch/nn.py:412: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at /opt/conda/conda-bld/pytorch_1704987296916/work/aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  outputs = tnn.conv2d(


259/259 ━━━━━━━━━━━━━━━━━━━━ 67s 257ms/step - accuracy: 0.9362 - loss: 0.1886 - total_0-1_loss: 83.3462 - val_accuracy: 0.9932 - val_loss: 0.0420 - val_total_0-1_loss: 4.0000
Epoch 2/5
259/259 ━━━━━━━━━━━━━━━━━━━━ 64s 246ms/step - accuracy: 0.9802 - loss: 0.0597 - total_0-1_loss: 37.0462 - val_accuracy: 0.9949 - val_loss: 0.0325 - val_total_0-1_loss: 3.0000
Epoch 3/5
259/259 ━━━━━━━━━━━━━━━━━━━━ 64s 249ms/step - accuracy: 0.9869 - loss: 0.0463 - total_0-1_loss: 28.1000 - val_accuracy: 0.9949 - val_loss: 0.0302 - val_total_0-1_loss: 3.0000
Epoch 4/5
259/259 ━━━━━━━━━━━━━━━━━━━━ 64s 247ms/step - accuracy: 0.9895 - loss: 0.0442 - total_0-1_loss: 24.6269 - val_accuracy: 0.9949 - val_loss: 0.0255 - val_total_0-1_loss: 3.0000
Epoch 5/5
259/259 ━━━━━━━━━━━━━━━━━━━━ 66s 256ms/step - accuracy: 0.9854 - loss: 0.0402 - total_0-1_loss: 28.6192 - val_accuracy: 0.9949 - val_loss: 0.0245 - val_total_0-1_loss: 3.0000


In [12]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

OutOfMemoryError: Exception encountered when calling Activation.call().

[1mCUDA out of memory. Tried to allocate 44.00 MiB. GPU 0 has a total capacity of 7.75 GiB of which 44.88 MiB is free. Including non-PyTorch memory, this process has 6.28 GiB memory in use. Of the allocated memory 5.71 GiB is allocated by PyTorch, and 361.16 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)[0m

Arguments received by Activation.call():
  • inputs=torch.Tensor(shape=torch.Size([16, 149, 149, 32]), dtype=float32)

### 1.2.3 - Free the network and final training 
I'd really like to do this step but we run OOM.
The performance of the network still is good enough (we have a loss of only 0.02 on test) so
we can stop there with an acceptable model.

## 1.3 - K Fold Cross Validation

In [4]:
k = 5

### 1.3.1 - Data Loading

In [5]:
from torch.utils.data import DataLoader, ConcatDataset
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((299, 299))
full_dataset = ConcatDataset([train, test])

k_fold_manager = KFoldDatasetWrapper(k)
k_fold_manager.load_data(full_dataset)

### Procedure

In [6]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

learning_parameters = SgdLearningParameters(learning_rate=0.01, momentum=0.9, metrics=["accuracy", ZeroOneLoss()])

In [7]:
results, test_fold_sizes = k_fold_manager.run_k_fold_cv(learning_parameters, XceptionAugmented(), (3, 299, 299),
                                                        batch_size=16)

Starting procedure for fold 0
Epoch 1/80
  1/259 ━━━━━━━━━━━━━━━━━━━━ 2:33 593ms/step - accuracy: 0.3750 - loss: 0.8707 - total_0-1_loss: 10.0000

/home/jacopo/miniconda3/envs/keras-pytorch/lib/python3.12/site-packages/keras/src/backend/torch/nn.py:412: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at /opt/conda/conda-bld/pytorch_1704987296916/work/aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  outputs = tnn.conv2d(


259/259 ━━━━━━━━━━━━━━━━━━━━ 57s 219ms/step - accuracy: 0.9176 - loss: 0.1824 - total_0-1_loss: 110.3615 - val_accuracy: 0.9746 - val_loss: 0.0566 - val_total_0-1_loss: 15.0000
Epoch 2/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 56s 218ms/step - accuracy: 0.9740 - loss: 0.0670 - total_0-1_loss: 52.3154 - val_accuracy: 0.9780 - val_loss: 0.0367 - val_total_0-1_loss: 13.0000
Epoch 3/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 56s 218ms/step - accuracy: 0.9776 - loss: 0.0603 - total_0-1_loss: 47.6577 - val_accuracy: 0.9915 - val_loss: 0.0289 - val_total_0-1_loss: 5.0000
Epoch 4/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 57s 219ms/step - accuracy: 0.9807 - loss: 0.0494 - total_0-1_loss: 37.8423 - val_accuracy: 0.9898 - val_loss: 0.0345 - val_total_0-1_loss: 6.0000
Epoch 5/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 57s 220ms/step - accuracy: 0.9789 - loss: 0.0541 - total_0-1_loss: 42.0192 - val_accuracy: 0.9882 - val_loss: 0.0285 - val_total_0-1_loss: 7.0000
Epoch 6/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 56s 216ms/step - accuracy: 0.9805 - lo

In [8]:
import numpy as np
import pandas as pd

dataframe = pd.DataFrame(results)
dataframe.columns = ["loss", "accuracy", "0-1-loss"]

# To measure 0-1 loss correctly
dataframe["test_size"] = test_fold_sizes
dataframe["0-1-scaled-loss"] = dataframe["0-1-loss"] / dataframe["test_size"]

In [9]:
dataframe

loss  accuracy  0-1-loss  test_size  0-1-scaled-loss
0  0.014578  0.995777       5.0       1184         0.004223
1  0.026921  0.989020      13.0       1184         0.010980
2  0.034157  0.986475      16.0       1183         0.013525
3  0.041543  0.984784      18.0       1183         0.015216
4  0.019799  0.993238       8.0       1183         0.006762

In [10]:
np.average(dataframe[["loss", "accuracy", "0-1-scaled-loss"]], axis=0)

array([0.02739943, 0.98985887, 0.01014113])

In [11]:
dataframe.to_csv(f"{project_definition["name"]}_k_fold_cv.csv", index=False)

# 2- VGG-16
https://arxiv.org/abs/1409.1556

In [38]:
project_definition: dict[str, any] = {"name": "vgg16"}
default_values = {"batch_size": 32, "epochs": 15, "learning_rate": 1e-2}

In [39]:
import keras

# Setting weights of course requires downloading them from the source (Keras is our mirror as we work with their libraries)
untouched_vgg16 = keras.applications.vgg16.VGG16(weights='imagenet')

In [40]:
import numpy


def evaluate_vgg16(image, vgg16, verbose: bool = False):
    local_image = torch.permute(image, (1, 2, 0))
    local_image = numpy.expand_dims(local_image, 0)

    local_image = local_image * 255  # Workaround for the torch env and our loader

    local_image = keras.applications.vgg16.preprocess_input(local_image)
    return keras.applications.vgg16.decode_predictions(vgg16.predict(local_image, verbose=verbose), top=3)[0]

## 2.1 - Data loading for VGG-16

In [41]:
from torch.utils.data import DataLoader
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper
import torch

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((224, 224))
train, validation = torch.utils.data.random_split(train, [0.875, 0.125])

train_dataloader = DataLoader(dataset=train, batch_size=default_values["batch_size"], shuffle=True)
validation_dataloader = DataLoader(dataset=validation, batch_size=default_values["batch_size"], shuffle=True)
test_dataloader = DataLoader(dataset=test, batch_size=default_values["batch_size"], shuffle=True)

## 2.1 -Model evaulation without training

In [42]:
print_evaluation_lists_information(make_evaluations_list(evaluate_vgg16, untouched_vgg16, train))

For facet 0 model has predicted: ['pizza', 'bagel', 'French_loaf']. The correct label is 1
For facet 1 model has predicted: ['trifle', 'strawberry', 'bakery']. The correct label is 1
For facet 2 model has predicted: ['bakery', 'conch', 'potpie']. The correct label is 1
For facet 3 model has predicted: ['bagel', 'plate', 'tray']. The correct label is 1
For facet 4 model has predicted: ['Chihuahua', 'wallaby', 'gazelle']. The correct label is 0
For facet 5 model has predicted: ['French_bulldog', 'Chihuahua', 'boxer']. The correct label is 0
For facet 6 model has predicted: ['potpie', 'plate', 'bakery']. The correct label is 1
For facet 7 model has predicted: ['puck', 'tray', 'plate']. The correct label is 1


In [43]:
def evaluate_vgg16(image, vgg16, verbose: bool = False):
    local_image = torch.permute(image, (1, 2, 0))
    local_image = numpy.expand_dims(local_image, 0)

    return keras.applications.vgg16.decode_predictions(vgg16.predict(local_image, verbose=verbose), top=3)[0]

In [44]:
predictions: list[tuple[list, int]] = [(evaluate_vgg16(i[0], untouched_vgg16), i[1]) for i in test]

In [45]:
label_mappings = {0: ["chihuahua", "dog"], 1: ["muffin", "bakery"]}
TP = 0  # True positives
for i in range(len(predictions)):
    predicted_values = [j[1].lower() for j in predictions[i][0]]
    true_label = label_mappings[predictions[i][1]]

    TP += 1 if set(predicted_values) & set(true_label) else 0

precision = TP / len(predictions)
precision  # On the top 3 considering the fact that many miss classifications happen for the fact that the labels are more accurate for the dogs (some samples in the training set are not chihuahuas) and that Muffins do not have a real label.

0.0

## 2.2 - Fine tuning the model

### 2.2.1 -  Model definition

In [46]:
from models.structure.base_model_wrapper import BaseModelWrapper

import keras


# https://keras.io/guides/transfer_learning/#the-typical-transferlearning-workflow 
class VGG16Custom(BaseModelWrapper):
    latest_model: Functional

    def make_layers(self, input_shape: (int, int, int)) -> tuple[keras.Layer, keras.Layer]:
        C, W, H = input_shape

        inputs = keras.Input(input_shape)
        x = keras.layers.Permute((2, 3, 1))(inputs)

        # Augmentation process.
        x = keras.layers.RandomFlip(mode="horizontal_and_vertical")(x)
        x = keras.layers.RandomRotation(0.3)(x)
        x = keras.layers.RandomBrightness(0.4, value_range=(0., 1.))(x)

        x = keras.layers.Rescaling(255)(x)  # Avoid torch problem
        x = keras.applications.vgg16.preprocess_input(x)

        self.latest_model = keras.applications.vgg16.VGG16(
            weights='imagenet', include_top=False, input_shape=(W, H, C)
        )

        self.latest_model.trainable = False
        x = self.latest_model(x, training=False)
        x = keras.layers.GlobalAveragePooling2D()(x)

        outputs = keras.layers.Dense(1, activation='sigmoid')(x)
        return inputs, outputs

### 2.2.2. - Training and evaluation on frozen base model

In [47]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

vgg_custom_wrapper = VGG16Custom()
model = vgg_custom_wrapper.make_model((3, 224, 224))

learning_parameters = SgdLearningParameters(learning_rate=0.01, momentum=0.9, metrics=["accuracy", ZeroOneLoss()])
learning_parameters.compile_model(model)

model.summary()

Model: "functional_15"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_17      │ (None, 3, 224,    │          0 │ -                 │
│ (InputLayer)        │ 224)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ permute_8 (Permute) │ (None, 224, 224,  │          0 │ input_layer_17[0… │
│                     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_flip_8       │ (None, 224, 224,  │          0 │ permute_8[0][0]   │
│ (RandomFlip)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_rotation_8   │ (None, 224, 224,  │          0 │ random_flip_8[0]… │
│ (RandomRotation)    │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_brightness_8 │ (None, 224, 224,  │          0 │ random_rotation_… │
│ (RandomBrightness)  │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling_7         │ (None, 224, 224,  │          0 │ random_brightnes… │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item_6          │ (None, 224, 224)  │          0 │ rescaling_7[0][0] │
│ (GetItem)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item_7          │ (None, 224, 224)  │          0 │ rescaling_7[0][0] │
│ (GetItem)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item_8          │ (None, 224, 224)  │          0 │ rescaling_7[0][0] │
│ (GetItem)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stack_2 (Stack)     │ (None, 224, 224,  │          0 │ get_item_6[0][0], │
│                     │ 3)                │            │ get_item_7[0][0], │
│                     │                   │            │ get_item_8[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_62 (Add)        │ (None, 224, 224,  │          0 │ stack_2[0][0]     │
│                     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ vgg16 (Functional)  │ (None, 7, 7, 512) │ 14,714,688 │ add_62[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ global_average_poo… │ (None, 512)       │          0 │ vgg16[0][0]       │
│ (GlobalAveragePool… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_7 (Dense)     │ (None, 1)         │        513 │ global_average_p… │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 14,715,201 (56.13 MB)

 Trainable params: 513 (2.00 KB)

 Non-trainable params: 14,714,688 (56.13 MB)

In [48]:
history = model.fit(train_dataloader, epochs=5, validation_data=validation_dataloader, callbacks=[])

Epoch 1/5
130/130 ━━━━━━━━━━━━━━━━━━━━ 59s 457ms/step - accuracy: 0.9326 - loss: 0.4520 - total_0-1_loss: 104.5038 - val_accuracy: 0.9915 - val_loss: 0.0554 - val_total_0-1_loss: 5.0000
Epoch 2/5
130/130 ━━━━━━━━━━━━━━━━━━━━ 57s 436ms/step - accuracy: 0.9672 - loss: 0.2194 - total_0-1_loss: 68.9695 - val_accuracy: 0.9780 - val_loss: 0.2682 - val_total_0-1_loss: 13.0000
Epoch 3/5
130/130 ━━━━━━━━━━━━━━━━━━━━ 57s 440ms/step - accuracy: 0.9712 - loss: 0.2104 - total_0-1_loss: 55.8015 - val_accuracy: 0.9898 - val_loss: 0.0639 - val_total_0-1_loss: 6.0000
Epoch 4/5
130/130 ━━━━━━━━━━━━━━━━━━━━ 57s 438ms/step - accuracy: 0.9777 - loss: 0.1353 - total_0-1_loss: 47.0382 - val_accuracy: 0.9898 - val_loss: 0.0743 - val_total_0-1_loss: 6.0000
Epoch 5/5
130/130 ━━━━━━━━━━━━━━━━━━━━ 57s 436ms/step - accuracy: 0.9780 - loss: 0.1661 - total_0-1_loss: 47.7252 - val_accuracy: 0.9932 - val_loss: 0.0357 - val_total_0-1_loss: 4.0000


In [49]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

37/37 ━━━━━━━━━━━━━━━━━━━━ 14s 371ms/step - accuracy: 0.9912 - loss: 0.0661 - total_0-1_loss: 4.7895
Test accuracy is 99.24% while loss is 0.06904620677232742


### 2.2.3 - Fine tuning on the whole structure 

In [50]:
vgg_custom_wrapper.latest_model.trainable = True
model.compile(optimizer=keras.optimizers.Adam(1e-5), loss="binary_crossentropy", metrics=["accuracy"])

model.fit(train_dataloader, epochs=10, validation_data=validation_dataloader, callbacks=[
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=5, verbose=0, mode="min"),
])

Epoch 1/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 596ms/step - accuracy: 0.9684 - loss: 0.1729 - val_accuracy: 0.9848 - val_loss: 0.0491
Epoch 2/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 601ms/step - accuracy: 0.9837 - loss: 0.0596 - val_accuracy: 0.9898 - val_loss: 0.0322
Epoch 3/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 597ms/step - accuracy: 0.9858 - loss: 0.0509 - val_accuracy: 0.9966 - val_loss: 0.0150
Epoch 4/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 596ms/step - accuracy: 0.9884 - loss: 0.0351 - val_accuracy: 0.9898 - val_loss: 0.0302
Epoch 5/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 79s 604ms/step - accuracy: 0.9931 - loss: 0.0222 - val_accuracy: 0.9898 - val_loss: 0.0348
Epoch 6/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 603ms/step - accuracy: 0.9889 - loss: 0.0493 - val_accuracy: 0.9932 - val_loss: 0.0140
Epoch 7/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 597ms/step - accuracy: 0.9950 - loss: 0.0146 - val_accuracy: 0.9898 - val_loss: 0.0312
Epoch 8/10
130/130 ━━━━━━━━━━━━━━━━━━━━ 78s 601ms/step - accuracy: 0.9954 - loss: 0

In [51]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

37/37 ━━━━━━━━━━━━━━━━━━━━ 14s 362ms/step - accuracy: 0.9891 - loss: 0.0191
Test accuracy is 99.16% while loss is 0.019587907940149307


In [ ]:
# TODO FInish
# But well done! Vgg16 is op for now in our problem domani!

## 2.3 - K fold CV

In [52]:
k = 5

### 1.3.1 - Data Loading

In [53]:
from torch.utils.data import DataLoader, ConcatDataset
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((224, 224))
full_dataset = ConcatDataset([train, test])

k_fold_manager = KFoldDatasetWrapper(k)
k_fold_manager.load_data(full_dataset)

### Procedure

In [54]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

learning_parameters = SgdLearningParameters(learning_rate=0.01, momentum=0.9, metrics=["accuracy", ZeroOneLoss()])

In [55]:
results, test_fold_sizes = k_fold_manager.run_k_fold_cv(learning_parameters, VGG16Custom(), (3, 224, 224),
                                                        batch_size=16)

Starting procedure for fold 0
Epoch 1/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 57s 221ms/step - accuracy: 0.9241 - loss: 0.5028 - total_0-1_loss: 117.6231 - val_accuracy: 0.9814 - val_loss: 0.2249 - val_total_0-1_loss: 11.0000
Epoch 2/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 59s 227ms/step - accuracy: 0.9557 - loss: 0.4099 - total_0-1_loss: 82.1231 - val_accuracy: 0.9915 - val_loss: 0.0763 - val_total_0-1_loss: 5.0000
Epoch 3/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 57s 222ms/step - accuracy: 0.9696 - loss: 0.3373 - total_0-1_loss: 65.1885 - val_accuracy: 0.9915 - val_loss: 0.1023 - val_total_0-1_loss: 5.0000
Epoch 4/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 59s 228ms/step - accuracy: 0.9744 - loss: 0.2844 - total_0-1_loss: 53.3346 - val_accuracy: 0.9932 - val_loss: 0.0828 - val_total_0-1_loss: 4.0000
Epoch 5/80
259/259 ━━━━━━━━━━━━━━━━━━━━ 58s 222ms/step - accuracy: 0.9783 - loss: 0.2380 - total_0-1_loss: 43.9962 - val_accuracy: 0.9915 - val_loss: 0.1043 - val_total_0-1_loss: 5.0000
Epoch 6/80
259/259 ━━━━━━━━━━━━━━━━━━━

In [56]:
import numpy as np
import pandas as pd

dataframe = pd.DataFrame(results)
dataframe.columns = ["loss", "accuracy", "0-1-loss"]

# To measure 0-1 loss correctly
dataframe["test_size"] = test_fold_sizes
dataframe["0-1-scaled-loss"] = dataframe["0-1-loss"] / dataframe["test_size"]

In [59]:
dataframe

loss  accuracy  0-1-loss  test_size  0-1-scaled-loss
0  0.145387  0.988176      14.0       1184         0.011824
1  0.094814  0.991554      10.0       1184         0.008446
2  0.070941  0.994928       6.0       1183         0.005072
3  0.149737  0.987320      15.0       1183         0.012680
4  0.118373  0.990702      11.0       1183         0.009298

In [60]:
np.average(dataframe[["loss", "accuracy", "0-1-scaled-loss"]], axis=0)

array([0.11585023, 0.99053597, 0.00946403])

In [58]:
dataframe.to_csv(f"{project_definition["name"]}_k_fold_cv.csv", index=False)